## <center> Opening a Chinese Restaurant in DC </center>

<center> In this notebook I will be explaining and extracting data from websites like dc.gov and foursquare to determine the best place to start a business, specifically a chinese restaurant </center>

### Data Defined:

Below I will be importing the 2019 crime rates database from https://dc.gov/ website, cleaning up the database and then displaying it. With this data, we can factor it in to our decision as to where the best place to put our new business.

In [1]:
#Import to read dataframe
import types
import numpy as np # library to handle data in a vectorized manner
import pandas as pd
from botocore.client import Config
import ibm_boto3

In [2]:
# The code was removed by Watson Studio for sharing.

### Lets take a look at the data in the database

In [3]:
df_data_1 = pd.read_csv(body)
df_data_1.head()

CCN       OFFENSE                                   BLOCK  WARD ANC  \
0  17084415      HOMICIDE  130 - 199 BLOCK OF IRVINGTON STREET SW     8  8D   
1  18208996   THEFT/OTHER          2400 BLOCK OF MARKET STREET NE     5  5C   
2  18204218  THEFT F/AUTO          900 - 999 BLOCK OF G STREET NW     2  2C   
3  19005282       ROBBERY  4800 - 4899 BLOCK OF CENTRAL AVENUE NE     7  7C   
4  19005286      BURGLARY  4700 - 4798 BLOCK OF EASTERN AVENUE NE     5  5B   

   DISTRICT    PSA NEIGHBORHOOD_CLUSTER BLOCK_GROUP   LATITUDE  LONGITUDE  \
0       7.0  708.0           Cluster 39    010900 2  38.820461 -77.010375   
1       5.0  503.0           Cluster 24    009000 1  38.920536 -76.952663   
2       2.0  209.0            Cluster 8    005800 1  38.898310 -77.024958   
3       6.0  608.0           Cluster 33    007804 3  38.890393 -76.933411   
4       4.0  405.0           Cluster 20    009503 1  38.946920 -76.979005   

    OBJECTID OCTO_RECORD_ID  
0  305273937    17084415-01  
1  305329181    18208996-01  
2  305331558    18204218-01  
3  305332216    19005282-01  
4  305332217    19005286-01

#### I am going to take the data and sort the crimes into wards. DC is split up into 8 wards, which sorting it in these categories will allow us to determine how many crimes happen in each ward.

In [4]:
#Create new dataframe with incidents by ward
df_incidents = df_data_1.groupby(['WARD']).size().reset_index(name="Count")

In [5]:
df_incidents

WARD  Count
0     1   1996
1     2   2998
2     3    920
3     4   1087
4     5   2152
5     6   2338
6     7   1635
7     8   1255

### As we can see, ward 2 in DC has the highest number of crimes in 2019. Now, we're going to import folium and visualize it for us to see.

In [6]:
!conda install -c conda-forge folium=0.5.0 --yes #install folium
import folium

Solving environment: done

# All requested packages already installed.



In [7]:
#Put everything into a map
# download countries geojson file NEED THIS FOR DEFINING AREAS/BOUNDARIES
!wget --quiet "http://data.codefordc.org/dataset/a9512704-4ece-47cd-b3c0-402d28609364/resource/8ca2fd50-06cc-497f-89f9-a7937ff3650d/download/washington-dc-wards-2012.geojson"
    
print('GeoJSON file downloaded!')

GeoJSON file downloaded!


In [8]:
world_geo = r'washington-dc-wards-2012.geojson' # geojson file to get the borders of the wards


# Washington DC latitude and longitude values
latitude = 38.91
longitude = -77.04

# create a plain world map
world_map = folium.Map(location=[latitude, longitude], zoom_start=12)
world_map.choropleth(
    geo_data=world_geo,
    data=df_incidents,
    columns=['WARD', 'Count'],
    key_on='feature.properties.WARD',
    #threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Crime Rates in Washington DC',
    reset=True
)
world_map

### Explanation of Data

As you can see above, the data is split up into the 8 wards, just like how DC is. Now that we have the data where the crime rates are generally located, we can now incorporate the Foursquare data to provide us with average reviews of restaurants and business within these districts, as well as type of business (i.e. restaurant, office building, hotel).

## <center> Utilizing Foursquare to find restaurants in each ward </center>

### First lets put our Foursquare Credentials here

In [9]:
import requests # library to handle requests
from pandas.io.json import json_normalize# tranforming json file into a pandas dataframe library
# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
CLIENT_ID = '1YZGINGMDDORH40PP2QN0WWPUDY5JXBOT5TL3MNKCU4NG0SN' # your Foursquare ID
CLIENT_SECRET = 'KMSKN0NBS15INTGFPDQC4QMYE3NVJED0XT0C5FAB0KPGJHBM' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1YZGINGMDDORH40PP2QN0WWPUDY5JXBOT5TL3MNKCU4NG0SN
CLIENT_SECRET:KMSKN0NBS15INTGFPDQC4QMYE3NVJED0XT0C5FAB0KPGJHBM


### Below we will use the coordinates of the center of DC so we can find all the businesses. We put it in a url to query in Foursquare

In [10]:
# Washington DC latitude and longitude values
latitude = 38.91
longitude = -77.04

LIMIT = 300 # limit of number of venues returned by Foursquare API
radius = 3500 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
url # display URL




'https://api.foursquare.com/v2/venues/explore?&client_id=1YZGINGMDDORH40PP2QN0WWPUDY5JXBOT5TL3MNKCU4NG0SN&client_secret=KMSKN0NBS15INTGFPDQC4QMYE3NVJED0XT0C5FAB0KPGJHBM&v=20180604&ll=38.91,-77.04&radius=3500&limit=300'

### This section will provide the response of the query in JSON format, which will be cleaned up into usable data

In [11]:
results = requests.get(url).json() #results will display the query request response

In [12]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']



### Below we normalize the JSON to pull out the information necessary to answer our questions

In [13]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng', 'venue.location.postalCode']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name        categories        lat        lng postalCode
0  Duke's Grocery         Gastropub  38.910187 -77.038262      20036
1            Komi  Greek Restaurant  38.910058 -77.038231      20036
2  Keegan Theatre           Theater  38.910346 -77.039933      20036
3    Little Serow   Thai Restaurant  38.910135 -77.038357      20036
4   Dupont Circle              Park  38.909704 -77.043783      20036

In [14]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=13) # generate map centred around the DC
x = -1
venues_map.choropleth(
    geo_data=world_geo,
    data=df_incidents,
    columns=['WARD', 'Count'],
    key_on='feature.properties.WARD',
    #threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Crime Rates in Washington DC',
    reset=True
)
# add the businesses as blue circle markers
for lat, lng, name in zip(nearby_venues.lat, nearby_venues.lng, nearby_venues.name):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=str(name.replace("'", "").replace('"', "")), 
        fill = False,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

### As you see above there are some clusters of Asian businesses. We can hone in on these areas by using k-means clustering to find out a good location to put a Chinese restaurant that will guarentee business. We will begin by importing the libraries to handle clustering

In [15]:
import matplotlib.pyplot as plt # plotting library
# backend for rendering plots within the browser
%matplotlib inline 
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans 
from sklearn.datasets.samples_generator import make_blobs

### Lets quickly check the size of our dataframe

In [16]:
print(nearby_venues.shape)

(100, 5)


### Group the businesses by area code

In [17]:
nearby_venues.groupby('postalCode').count()

name  categories  lat  lng
postalCode                            
20001         15          15   15   15
20002          1           1    1    1
20004          1           1    1    1
20005         13          13   13   13
20006          7           7    7    7
20007          3           3    3    3
20008          1           1    1    1
20009         31          31   31   31
20009-4307     1           1    1    1
20036         15          15   15   15
20037          6           6    6    6
20052          1           1    1    1
20071          1           1    1    1
20500          3           3    3    3

### Let's find out how many unique business categories we have

In [18]:
print('There are {} uniques categories.'.format(len(nearby_venues['categories'].unique())))

There are 53 uniques categories.


### Time to analyze each zip code for what is the most popular business

In [19]:
# one hot encoding
dc_onehot = pd.get_dummies(nearby_venues[['categories']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
dc_onehot['postalCode'] = nearby_venues['postalCode'] 

# move postalcode column to the first column
fixed_columns = [dc_onehot.columns[-1]] + list(dc_onehot.columns[:-1])
dc_onehot = dc_onehot[fixed_columns]

dc_onehot.head()

postalCode  Afghan Restaurant  American Restaurant  Art Gallery  Art Museum  \
0      20036                  0                    0            0           0   
1      20036                  0                    0            0           0   
2      20036                  0                    0            0           0   
3      20036                  0                    0            0           0   
4      20036                  0                    0            0           0   

   Bakery  Beer Bar  Beer Garden  Bookstore  Cocktail Bar     ...       \
0       0         0            0          0             0     ...        
1       0         0            0          0             0     ...        
2       0         0            0          0             0     ...        
3       0         0            0          0             0     ...        
4       0         0            0          0             0     ...        

   Seafood Restaurant  Spanish Restaurant  Steakhouse  Thai Restaurant  \
0                   0                   0           0                0   
1                   0                   0           0                0   
2                   0                   0           0                0   
3                   0                   0           0                1   
4                   0                   0           0                0   

   Theater  Trail  Whisky Bar  Wine Bar  Wine Shop  Yoga Studio  
0        0      0           0         0          0            0  
1        0      0           0         0          0            0  
2        1      0           0         0          0            0  
3        0      0           0         0          0            0  
4        0      0           0         0          0            0  

[5 rows x 54 columns]

### Next, lets group rows by postal code and by taking the mean of the frequency of occurrence of each category

In [20]:
dc_grouped = dc_onehot.groupby('postalCode').mean().reset_index()
dc_grouped

postalCode  Afghan Restaurant  American Restaurant  Art Gallery  \
0        20001           0.000000             0.066667     0.000000   
1        20002           0.000000             0.000000     0.000000   
2        20004           0.000000             0.000000     0.000000   
3        20005           0.000000             0.076923     0.000000   
4        20006           0.000000             0.142857     0.000000   
5        20007           0.000000             0.000000     0.000000   
6        20008           0.000000             0.000000     0.000000   
7        20009           0.032258             0.064516     0.032258   
8   20009-4307           0.000000             0.000000     0.000000   
9        20036           0.000000             0.000000     0.000000   
10       20037           0.000000             0.000000     0.000000   
11       20052           0.000000             0.000000     0.000000   
12       20071           0.000000             0.000000     0.000000   
13       20500           0.000000             0.000000     0.000000   

    Art Museum    Bakery  Beer Bar  Beer Garden  Bookstore  Cocktail Bar  \
0     0.000000  0.066667  0.000000     0.066667   0.000000      0.066667   
1     0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
2     0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
3     0.000000  0.000000  0.076923     0.000000   0.000000      0.000000   
4     0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
5     0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
6     0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
7     0.032258  0.000000  0.000000     0.000000   0.000000      0.064516   
8     0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
9     0.000000  0.000000  0.000000     0.000000   0.133333      0.000000   
10    0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
11    0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
12    0.000000  0.000000  0.000000     0.000000   0.000000      0.000000   
13    0.333333  0.000000  0.000000     0.000000   0.000000      0.000000   

       ...       Seafood Restaurant  Spanish Restaurant  Steakhouse  \
0      ...                 0.000000            0.000000    0.000000   
1      ...                 0.000000            1.000000    0.000000   
2      ...                 0.000000            0.000000    0.000000   
3      ...                 0.076923            0.000000    0.076923   
4      ...                 0.000000            0.000000    0.000000   
5      ...                 0.000000            0.000000    0.000000   
6      ...                 0.000000            0.000000    0.000000   
7      ...                 0.000000            0.000000    0.000000   
8      ...                 1.000000            0.000000    0.000000   
9      ...                 0.000000            0.066667    0.000000   
10     ...                 0.000000            0.000000    0.000000   
11     ...                 0.000000            0.000000    0.000000   
12     ...                 0.000000            0.000000    0.000000   
13     ...                 0.000000            0.000000    0.000000   

    Thai Restaurant   Theater  Trail  Whisky Bar  Wine Bar  Wine Shop  \
0          0.000000  0.000000    0.0    0.000000  0.066667   0.066667   
1          0.000000  0.000000    0.0    0.000000  0.000000   0.000000   
2          0.000000  0.000000    0.0    0.000000  0.000000   0.000000   
3          0.000000  0.076923    0.0    0.000000  0.000000   0.000000   
4          0.000000  0.000000    0.0    0.000000  0.000000   0.000000   
5          0.000000  0.000000    0.0    0.000000  0.000000   0.000000   
6          0.000000  0.000000    1.0    0.000000  0.000000   0.000000   
7          0.032258  0.000000    0.0    0.032258  0.032258   0.000000   
8          0.000000  0.000000    0.0    0.000000  0.000000   0.000000   
9

### Now let's show the top 5 most common businesses in each postal code

In [21]:
num_top_venues = 5

for hood in dc_grouped['postalCode']:
    print("----"+hood+"----")
    temp = dc_grouped[dc_grouped['postalCode'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----20001----
                         venue  freq
0           Italian Restaurant  0.07
1               Ice Cream Shop  0.07
2               Sandwich Place  0.07
3                Movie Theater  0.07
4  Eastern European Restaurant  0.07


----20002----
                venue  freq
0  Spanish Restaurant   1.0
1   Afghan Restaurant   0.0
2          Restaurant   0.0
3  Israeli Restaurant   0.0
4  Italian Restaurant   0.0


----20004----
                venue  freq
0               Hotel   1.0
1   Afghan Restaurant   0.0
2          Restaurant   0.0
3  Israeli Restaurant   0.0
4  Italian Restaurant   0.0


----20005----
                 venue  freq
0                Hotel  0.23
1          Coffee Shop  0.15
2         Cycle Studio  0.08
3  American Restaurant  0.08
4             Beer Bar  0.08


----20006----
                 venue  freq
0                Hotel  0.29
1          Coffee Shop  0.29
2            Hotel Bar  0.14
3  American Restaurant  0.14
4    Indian Restaurant  0.14


----20007----


### I will now sort below to display the top ten venues for each postal code

In [22]:
# function to sort in descending order
def return_most_common_venues(row, num_top_venues): 
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [23]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['postalCode']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['postalCode'] = dc_grouped['postalCode']

for ind in np.arange(dc_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(dc_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

postalCode 1st Most Common Venue 2nd Most Common Venue  \
0        20001        Sandwich Place             Wine Shop   
1        20002    Spanish Restaurant           Yoga Studio   
2        20004                 Hotel           Yoga Studio   
3        20005                 Hotel           Coffee Shop   
4        20006           Coffee Shop                 Hotel   
5        20007                 Hotel    Falafel Restaurant   
6        20008                 Trail           Yoga Studio   
7        20009        Ice Cream Shop           Coffee Shop   
8   20009-4307    Seafood Restaurant           Yoga Studio   
9        20036             Bookstore                  Park   
10       20037                 Hotel     Indian Restaurant   
11       20052          College Quad           Yoga Studio   
12       20071           Coffee Shop           Yoga Studio   
13       20500            Art Museum   Government Building   

          3rd Most Common Venue 4th Most Common Venue  \
0   Eastern European Restaurant    Mexican Restaurant   
1                  Cycle Studio                   Gym   
2                           Gym         Grocery Store   
3                   Pizza Place            Steakhouse   
4                     Hotel Bar   American Restaurant   
5                 Deli / Bodega           Yoga Studio   
6                  Cycle Studio                   Gym   
7                 Grocery Store   American Restaurant   
8                  Cycle Studio                   Gym   
9            Spanish Restaurant    Israeli Restaurant   
10            French Restaurant           Salad Place   
11                Deli / Bodega                   Gym   
12                Deli / Bodega                   Gym   
13                         Park           Yoga Studio   

      5th Most Common Venue        6th Most Common Venue  \
0             Movie Theater           Italian Restaurant   
1             Grocery Store             Greek Restaurant   
2          Greek Restaurant          Government Building   
3        Salon / Barbershop                 Cycle Studio   
4         Indian Restaurant  Eastern European Restaurant   
5                       Gym                Grocery Store   
6             Grocery Store             Greek Restaurant   
7              Cocktail Bar                  Yoga Studio   
8             Grocery Store             Greek Restaurant   
9          Greek Restaurant                  Pizza Place   
10  New American Restaurant                          Gym   
11            Grocery Store             Greek Restaurant   
12            Grocery Store             Greek Restaurant   
13            Deli / Bodega                          Gym   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0             Ice Cream Shop           Coffee Shop          Cocktail Bar   
1        Government Building             Gastropub     French Restaurant   
2                  Gastropub     French Restaurant        Farmers Market   
3                   Beer Bar    Seafood Restaurant               Theater   
4                        Gym         Grocery Store      Greek Restaurant   
5           Greek Restaurant   Government Building             Gastropub   
6        Government Building             Gastropub     French Restaurant   
7   Mediterranean Restaurant           Art Gallery            Art Museum   
8        Government Building             Gastropub     French Restaurant   
9                Salad Place     Convenience Store        Sandwich Place   
10             Deli / Bodega         Grocery Store      Greek Restaurant   
11       Government Building             Gastropub     French Restaurant   
12       Government Building             Gastropub     French Restaurant   
13             Grocery Store      Greek Restaurant             Gastropub   

       10th Most Common Venue  
0   Latin American Restaurant  
1              Farmers Market  
2          Falafel Restaurant  
3         American Restaurant  
4         Gover

### Time to Cluster Neighborhoods!

I will be running K-means to cluster postalcodes into 10 clusters, which will make it easier to visualize business concentration

In [24]:
# set number of clusters
kclusters = 10

dc_grouped_clustering = dc_grouped.drop('postalCode', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(dc_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 6, 3, 7, 7, 9, 4, 1, 0, 1], dtype=int32)

Lets take the cluster and combine into a new dataframe with top 10 venues of each neighborhood

In [25]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

dc_merged = nearby_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
dc_merged = dc_merged.join(neighborhoods_venues_sorted.set_index('postalCode'), on='postalCode')



In [26]:
dc_merged

name  \
0                                      Duke's Grocery   
1                                                Komi   
2                                      Keegan Theatre   
3                                        Little Serow   
4                                       Dupont Circle   
5                       Kramerbooks & Afterwords Cafe   
6                      Dupont Circle FRESHFARM Market   
7                                          sweetgreen   
8                                  Second Story Books   
9                           Dolcezza Artisanal Gelato   
10                                               CAVA   
11                                      Bub and Pop's   
12                                           Boqueria   
13                                 Barcelona Wine Bar   
14                                        Zengo Cycle   
15                                     Logan 14 Aveda   
16                                            Estadio   
17                         Dolcezza Gelato and Coffee   
18                                 The Studio Theatre   
19                            The Phillips Collection   
20                                               Wawa   
21                                       Le Diplomate   
22                              ArtJamz Dupont Studio   
23                         Kimpton Mason & Rook Hotel   
24                               Glen's Garden Market   
25                           Rock Creek Running Trail   
26                    The Madison Washington DC Hotel   
27                                      Little Sesame   
28                                          ChurchKey   
29                                   Keren Restaurant   
..                                                ...   
70                                     Off the Record   
71                                              Supra   
72                                             El Sol   
73                                            Tortino   
74                         La Colombe Coffee Roasters   
75                                             Seylou   
76                                             Maydan   
77                                    The White House   
78                                          Rose Park   
79                       Marcel's by Robert Wiedmaier   
80                                             &pizza   
81                           North Lawn - White House   
82                         La Colombe Coffee Roasters   
83                                  The Columbia Room   
84                                            Donburi   
85                                GWU University Yard   
86                                          SUNdeVICH   
87                                       Maxwell Park   
88                                   Old Ebbitt Grill   
89                                       Tail Up Goat   
90                                         The Dabney   
91                                     Swing's Coffee   
92  The Willard InterContinental Washington D.C. H...   
93                                  Dacha Beer Garden   
94             George's King of Falafel & Cheesesteak   
95                           Stachowski Market & Deli   
96                                Reformation Fitness   
97                                         Grand Cata   
98                  Four Seasons Hotel Washington, DC   
99                  Landmark Atlantic Plumbing Cinema   

                     categories        lat        lng postalCode  \
0                     Gastropub  38.910187 -77.038262      20036   
1              Greek Restaurant  38.910058 -77.038231      20036   
2                       Theater  38.910346 -77.039933      20036   
3               Thai Restaurant  38.910135 -77.038357      20036   
4                          Park  38.909704 -77.043783      20036   
5                     Bookstore  38.910756 -77.043880      20036   
6                Farmers Market  38.91

Convert Cluster labels from float to int

In [27]:
dc_merged['Cluster Labels'].fillna(0, inplace=True)
dc_merged['Cluster Labels'] = dc_merged['Cluster Labels'].astype(int)
dc_merged

name  \
0                                      Duke's Grocery   
1                                                Komi   
2                                      Keegan Theatre   
3                                        Little Serow   
4                                       Dupont Circle   
5                       Kramerbooks & Afterwords Cafe   
6                      Dupont Circle FRESHFARM Market   
7                                          sweetgreen   
8                                  Second Story Books   
9                           Dolcezza Artisanal Gelato   
10                                               CAVA   
11                                      Bub and Pop's   
12                                           Boqueria   
13                                 Barcelona Wine Bar   
14                                        Zengo Cycle   
15                                     Logan 14 Aveda   
16                                            Estadio   
17                         Dolcezza Gelato and Coffee   
18                                 The Studio Theatre   
19                            The Phillips Collection   
20                                               Wawa   
21                                       Le Diplomate   
22                              ArtJamz Dupont Studio   
23                         Kimpton Mason & Rook Hotel   
24                               Glen's Garden Market   
25                           Rock Creek Running Trail   
26                    The Madison Washington DC Hotel   
27                                      Little Sesame   
28                                          ChurchKey   
29                                   Keren Restaurant   
..                                                ...   
70                                     Off the Record   
71                                              Supra   
72                                             El Sol   
73                                            Tortino   
74                         La Colombe Coffee Roasters   
75                                             Seylou   
76                                             Maydan   
77                                    The White House   
78                                          Rose Park   
79                       Marcel's by Robert Wiedmaier   
80                                             &pizza   
81                           North Lawn - White House   
82                         La Colombe Coffee Roasters   
83                                  The Columbia Room   
84                                            Donburi   
85                                GWU University Yard   
86                                          SUNdeVICH   
87                                       Maxwell Park   
88                                   Old Ebbitt Grill   
89                                       Tail Up Goat   
90                                         The Dabney   
91                                     Swing's Coffee   
92  The Willard InterContinental Washington D.C. H...   
93                                  Dacha Beer Garden   
94             George's King of Falafel & Cheesesteak   
95                           Stachowski Market & Deli   
96                                Reformation Fitness   
97                                         Grand Cata   
98                  Four Seasons Hotel Washington, DC   
99                  Landmark Atlantic Plumbing Cinema   

                     categories        lat        lng postalCode  \
0                     Gastropub  38.910187 -77.038262      20036   
1              Greek Restaurant  38.910058 -77.038231      20036   
2                       Theater  38.910346 -77.039933      20036   
3               Thai Restaurant  38.910135 -77.038357      20036   
4                          Park  38.909704 -77.043783      20036   
5                     Bookstore  38.910756 -77.043880      20036   
6                Farmers Market  38.91

### Time to visualize the clusters and see our dataset

In [28]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)
map_clusters.choropleth(
    geo_data=world_geo,
    data=df_incidents,
    columns=['WARD', 'Count'],
    key_on='feature.properties.WARD',
    #threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.6, 
    line_opacity=0.2,
    legend_name='Crime Rates in Washington DC',
    reset=True
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(dc_merged['lat'], dc_merged['lng'], dc_merged['categories'], dc_merged['Cluster Labels']): #Changed dc_merged[2] to categories instead of postal code
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### What we can see above is that the concentration of most businesses is directly related to the crimes committed. Below I will display all the businesses within each cluster and dive into the information to help us determine the best place to put our restaurant.

In [29]:
dc_merged.loc[dc_merged['Cluster Labels'] == 0, dc_merged.columns[[1] + list(range(5, dc_merged.shape[1]))]]

categories  Cluster Labels 1st Most Common Venue  \
31  Seafood Restaurant               0    Seafood Restaurant   
78                Park               0                   NaN   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
31           Yoga Studio          Cycle Studio                   Gym   
78                   NaN                   NaN                   NaN   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
31         Grocery Store      Greek Restaurant   Government Building   
78                   NaN                   NaN                   NaN   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
31             Gastropub     French Restaurant         Farmers Market  
78                   NaN                   NaN                    NaN

In [30]:
dc_merged.loc[dc_merged['Cluster Labels'] == 1, dc_merged.columns[[4] + list(range(5, dc_merged.shape[1]))]]

postalCode  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0       20036               1             Bookstore                  Park   
1       20036               1             Bookstore                  Park   
2       20036               1             Bookstore                  Park   
3       20036               1             Bookstore                  Park   
4       20036               1             Bookstore                  Park   
5       20036               1             Bookstore                  Park   
6       20036               1             Bookstore                  Park   
7       20036               1             Bookstore                  Park   
8       20036               1             Bookstore                  Park   
9       20009               1        Ice Cream Shop           Coffee Shop   
10      20036               1             Bookstore                  Park   
11      20036               1             Bookstore                  Park   
12      20036               1             Bookstore                  Park   
13      20009               1        Ice Cream Shop           Coffee Shop   
17      20001               1        Sandwich Place             Wine Shop   
19      20009               1        Ice Cream Shop           Coffee Shop   
20      20036               1             Bookstore                  Park   
21      20009               1        Ice Cream Shop           Coffee Shop   
22      20009               1        Ice Cream Shop           Coffee Shop   
24      20009               1        Ice Cream Shop           Coffee Shop   
27      20036               1             Bookstore                  Park   
29      20009               1        Ice Cream Shop           Coffee Shop   
32      20009               1        Ice Cream Shop           Coffee Shop   
33      20036               1             Bookstore                  Park   
34      20009               1        Ice Cream Shop           Coffee Shop   
35      20009               1        Ice Cream Shop           Coffee Shop   
36      20009               1        Ice Cream Shop           Coffee Shop   
37      20009               1        Ice Cream Shop           Coffee Shop   
38      20009               1        Ice Cream Shop           Coffee Shop   
39      20009               1        Ice Cream Shop           Coffee Shop   
..        ...             ...                   ...                   ...   
41      20009               1        Ice Cream Shop           Coffee Shop   
42      20009               1        Ice Cream Shop           Coffee Shop   
43      20009               1        Ice Cream Shop           Coffee Shop   
44      20009               1        Ice Cream Shop           Coffee Shop   
48      20009               1        Ice Cream Shop           Coffee Shop   
52      20009               1        Ice Cream Shop           Coffee Shop   
56      20009               1        Ice Cream Shop           Coffee Shop   
62      20009               1        Ice Cream Shop           Coffee Shop   
64      20009               1        Ice Cream Shop           Coffee Shop   
65      20001               1        Sandwich Place             Wine Shop   
67      20009               1        Ice Cream Shop           Coffee Shop   
68      20009               1        Ice Cream Shop           Coffee Shop   
71      20001               1        Sandwich Place             Wine Shop   
72      20001               1        Sandwich Place             Wine Shop   
73      20001               1        Sandwich Place             Wine Shop   
74      20001               1        Sandwich Place             Wine Shop   
75      20001               1        Sandwich Place             Wine Shop   
76      20009               1        Ice Cream Shop           Coffee Shop   
80      20009               1        Ice Cream Shop           Coffee Shop   
82      20009               1        Ice Cream Shop           Coffee Shop   

In [31]:
dc_merged.loc[dc_merged['Cluster Labels'] == 2, dc_merged.columns[[4] + list(range(5, dc_merged.shape[1]))]]

postalCode  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
85      20052               2          College Quad           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
85         Deli / Bodega                   Gym         Grocery Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
85      Greek Restaurant   Government Building             Gastropub   

   9th Most Common Venue 10th Most Common Venue  
85     French Restaurant         Farmers Market

In [32]:
dc_merged.loc[dc_merged['Cluster Labels'] == 3, dc_merged.columns[[4] + list(range(5, dc_merged.shape[1]))]]

postalCode  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
92      20004               3                 Hotel           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
92                   Gym         Grocery Store      Greek Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
92   Government Building             Gastropub     French Restaurant   

   9th Most Common Venue 10th Most Common Venue  
92        Farmers Market     Falafel Restaurant

In [33]:
dc_merged.loc[dc_merged['Cluster Labels'] == 4, dc_merged.columns[[4] + list(range(5, dc_merged.shape[1]))]]

postalCode  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
25      20008               4                 Trail           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
25          Cycle Studio                   Gym         Grocery Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
25      Greek Restaurant   Government Building             Gastropub   

   9th Most Common Venue 10th Most Common Venue  
25     French Restaurant         Farmers Market

In [34]:
dc_merged.loc[dc_merged['Cluster Labels'] == 5, dc_merged.columns[[4] + list(range(5, dc_merged.shape[1]))]]

postalCode  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
53      20071               5           Coffee Shop           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
53         Deli / Bodega                   Gym         Grocery Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
53      Greek Restaurant   Government Building             Gastropub   

   9th Most Common Venue 10th Most Common Venue  
53     French Restaurant         Farmers Market

In [35]:
dc_merged.loc[dc_merged['Cluster Labels'] == 6, dc_merged.columns[[4] + list(range(5, dc_merged.shape[1]))]]

postalCode  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
16      20002               6    Spanish Restaurant           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
16          Cycle Studio                   Gym         Grocery Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
16      Greek Restaurant   Government Building             Gastropub   

   9th Most Common Venue 10th Most Common Venue  
16     French Restaurant         Farmers Market

### Cluster 7 Below looks promising. The data we see includes three separate zip codes (20005, 20006 and 20037) that have hotels as their 1st most common venue. Hotels means people who may not have the means to cook a meal and need to eat out.

In [36]:
dc_merged.loc[dc_merged['Cluster Labels'] == 7, dc_merged.columns[list(range(2, dc_merged.shape[1]))]]

lat        lng postalCode  Cluster Labels 1st Most Common Venue  \
14  38.910029 -77.032013      20005               7                 Hotel   
15  38.907861 -77.032158      20005               7                 Hotel   
18  38.909956 -77.031782      20005               7                 Hotel   
23  38.908047 -77.032911      20005               7                 Hotel   
26  38.905236 -77.034082      20005               7                 Hotel   
28  38.908510 -77.031709      20005               7                 Hotel   
30  38.905065 -77.048079      20037               7                 Hotel   
45  38.901041 -77.041680      20006               7           Coffee Shop   
46  38.900510 -77.036885      20006               7           Coffee Shop   
47  38.905701 -77.051075      20037               7                 Hotel   
49  38.904808 -77.048999      20037               7                 Hotel   
50  38.901483 -77.037692      20005               7                 Hotel   
51  38.905061 -77.049356      20037               7                 Hotel   
54  38.905401 -77.051326      20037               7                 Hotel   
55  38.900573 -77.044519      20006               7           Coffee Shop   
58  38.901522 -77.032230      20005               7                 Hotel   
59  38.902155 -77.032257      20005               7                 Hotel   
60  38.900199 -77.039970      20006               7           Coffee Shop   
61  38.899970 -77.040290      20006               7           Coffee Shop   
63  38.900478 -77.034006      20005               7                 Hotel   
66  38.900822 -77.038246      20006               7           Coffee Shop   
69  38.899984 -77.033939      20005               7                 Hotel   
70  38.900162 -77.036926      20006               7           Coffee Shop   
79  38.903433 -77.052226      20037               7                 Hotel   
88  38.897954 -77.033270      20005               7                 Hotel   
91  38.898073 -77.031991      20005               7                 Hotel   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
14           Coffee Shop           Pizza Place            Steakhouse   
15           Coffee Shop           Pizza Place            Steakhouse   
18           Coffee Shop           Pizza Place            Steakhouse   
23           Coffee Shop           Pizza Place            Steakhouse   
26           Coffee Shop           Pizza Place            Steakhouse   
28           Coffee Shop           Pizza Place            Steakhouse   
30     Indian Restaurant     French Restaurant           Salad Place   
45                 Hotel             Hotel Bar   American Restaurant   
46                 Hotel             Hotel Bar   American Restaurant   
47     Indian Restaurant     French Restaurant           Salad Place   
49     Indian Restaurant     French Restaurant           Salad Place   
50           Coffee Shop           Pizza Place            Steakhouse   
51     Indian Restaurant     French Restaurant           Salad Place   
54     Indian Restaurant     French Restaurant           Salad Place   
55                 Hotel             Hotel Bar   American Restaurant   
58           Coffee Shop           Pizza Place            Steakhouse   
59           Coffee Shop           Pizza Place            Steakhouse   
60                 Hotel             Hotel Bar   American Restaurant   
61                 Hotel             Hotel Bar   American Restaurant   
63           Coffee Shop           Pizza Place            Steakhouse   
66                 Hotel             Hotel Bar   American Restaurant   
69           Coffee Shop           Pizza Place            Steakhouse   
70                 Hotel             Hotel Bar   American Restaurant   
79     Indian Restaurant     French Restaurant           Salad Place   
88           Coffee Shop           Pizza Place            Steakhouse   
91           Coffee Shop           Pizza Place            

### Looking at the data the latitude and longitude of cluster 7 could be a good spot to do more research of businesses within the area to see if there is potential. I will be using the explore function from Foursquare below to check

In [37]:
lat_7 = 38.90
long_7 = -77.03
radius = 500 #500 meter radius

In [38]:
url_7 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, lat_7, long_7, VERSION, radius, LIMIT)
url_7

'https://api.foursquare.com/v2/venues/explore?client_id=1YZGINGMDDORH40PP2QN0WWPUDY5JXBOT5TL3MNKCU4NG0SN&client_secret=KMSKN0NBS15INTGFPDQC4QMYE3NVJED0XT0C5FAB0KPGJHBM&ll=38.9,-77.03&v=20180604&radius=500&limit=300'

#### Send GET request and examine results

In [39]:
results = requests.get(url_7).json()
'There are {} businesses in cluster 7'.format(len(results['response']['groups'][0]['items']))

'There are 100 businesses in cluster 7'

#### Get relevant part of JSON

In [40]:
items = results['response']['groups'][0]['items']
items[0]

{'reasons': {'count': 0,
  'items': [{'reasonName': 'globalInteractionReason',
    'summary': 'This spot is popular',
    'type': 'general'}]},
 'referralId': 'e-0-4b66f0bff964a52065312be3-0',
 'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/museum_art_',
     'suffix': '.png'},
    'id': '4bf58dd8d48988d18f941735',
    'name': 'Art Museum',
    'pluralName': 'Art Museums',
    'primary': True,
    'shortName': 'Art Museum'}],
  'id': '4b66f0bff964a52065312be3',
  'location': {'address': '1250 New York Ave NW',
   'cc': 'US',
   'city': 'Washington',
   'country': 'United States',
   'crossStreet': 'at 13th St NW',
   'distance': 63,
   'formattedAddress': ['1250 New York Ave NW (at 13th St NW)',
    'Washington, D.C. 20005',
    'United States'],
   'labeledLatLngs': [{'label': 'display',
     'lat': 38.89988597562643,
     'lng': -77.02927604118754}],
   'lat': 38.89988597562643,
   'lng': -77.02927604118754,
   'postalCode': '2

#### Process JSON and convert it to a clean dataframe

In [41]:
dataframe = json_normalize(items) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories'] + [col for col in dataframe.columns if col.startswith('venue.location.')] + ['venue.id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# filter the category for each row
dataframe_filtered['venue.categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean columns
dataframe_filtered.columns = [col.split('.')[-1] for col in dataframe_filtered.columns]

In [42]:
dataframe_filtered

name  \
0                National Museum of Women in the Arts   
1                                      Compass Coffee   
2                                 Mastro's Steakhouse   
3                                         Ocean Prime   
4                                      Swing's Coffee   
5                               Woodward Takeout Food   
6                                              Buredo   
7                                       District Taco   
8                     Dangerously Delicious Pie Truck   
9                                            Fruitive   
10                                             &pizza   
11                                          Five Guys   
12                    Astro Doughnuts & Fried Chicken   
13                                Blick Art Materials   
14                         The Oceanaire Seafood Room   
15                Washington Marriott at Metro Center   
16                                      Maison Kayser   
17                                       Panera Bread   
18                                          Toro Toro   
19            Joe's Seafood, Prime Steak & Stone Crab   
20                                        Cafe Mozart   
21                                           Sfoglina   
22                      Chop't Creative Salad Company   
23                                     PR at Partners   
24             Sofitel Washington DC Lafayette Square   
25                                   Old Ebbitt Grill   
26                                       The Hamilton   
27           Hilton Garden Inn Washington DC Downtown   
28  The Willard InterContinental Washington D.C. H...   
29                                 Shelly's Back Room   
..                                                ...   
70                                        Fig & Olive   
71                                The Round Robin Bar   
72                                         Occidental   
73                                   Ristorante Tosca   
74                                            Opaline   
75                                The Reliable Source   
76   Ford's Theater Center for Education & Leadership   
77                         Washington Wine And Liquor   
78                                          Starbucks   
79                                         The Mirror   
80                                Del Frisco's Grille   
81                         Stan's Restaurant & Lounge   
82                                      Louis Vuitton   
83                               Elizabeth's Gone Raw   
84                      Crunch Fitness - Metro Center   
85                             Potbelly Sandwich Shop   
86                                     The Bar Method   
87                                    JOE & THE JUICE   
88                                  Drafthouse Comedy   
89                                    Madame Tussauds   
90                                              Siroc   
91                                      Freedom Plaza   
92                                       Café du Parc   
93                             Potbelly Sandwich Shop   
94                                              Pinea   
95  Embassy Suites by Hilton Washington DC Convent...   
96                                     The Scotch Bar   
97                                   Lafayette Statue   
98                                     Petersen House   
99                                        Union Trust   

                       categories                         address  cc  \
0                      Art Museum            1250 New York Ave NW  US   
1                     Coffee Shop                    1401 I St NW  US   
2                      Steakhouse              600 13th Street NW  US   
3              Seafood Restaurant                    1341 G St NW  US   
4                     Coffee Shop                  640 14th St NW  US   
5                  Sandwich Place                    1426 H St NW  US   
6  

### Let's find out how many different types of businesses there are around cluster 7 and see if there's any chinese restaurants!

In [43]:
dataframe_filtered.groupby('categories').count()

name  address  cc  city  country  \
categories                                                          
American Restaurant                 4        4   4     4        4   
Art Museum                          1        1   1     1        1   
Arts & Crafts Store                 1        0   1     1        1   
Asian Restaurant                    1        1   1     1        1   
Bakery                              2        2   2     2        2   
Bar                                 2        2   2     2        2   
Belgian Restaurant                  1        1   1     1        1   
Brewery                             1        1   1     1        1   
Burger Joint                        1        1   1     1        1   
Camera Store                        1        1   1     1        1   
Coffee Shop                         4        4   4     4        4   
Comedy Club                         1        1   1     1        1   
Cosmetics Shop                      1        1   1     1        1   
Deli / Bodega                       1        1   1     1        1   
Donut Shop                          1        1   1     1        1   
Event Space                         1        1   1     1        1   
Farmers Market                      1        1   1     1        1   
Food Truck                          1        0   1     1        1   
French Restaurant                   3        3   3     3        3   
German Restaurant                   1        1   1     1        1   
Gym / Fitness Center                2        2   2     2        2   
History Museum                      1        0   1     1        1   
Hotel                               8        8   8     8        8   
Hotel Bar                           2        2   2     2        2   
Italian Restaurant                  5        5   5     5        5   
Juice Bar                           2        2   2     2        2   
Latin American Restaurant           1        1   1     1        1   
Leather Goods Store                 1        1   1     1        1   
Liquor Store                        1        1   1     1        1   
Lounge                              3        3   3     3        3   
Mediterranean Restaurant            2        2   2     2        2   
Mexican Restaurant                  1        1   1     1        1   
Monument / Landmark                 1        1   1     1        1   
Museum                              1        1   1     1        1   
New American Restaurant             1        1   1     1        1   
Nightclub                           2        2   2     2        2   
Nightlife Spot                      1        1   1     1        1   
Outdoor Sculpture                   1        1   1     1        1   
Performing Arts Venue               1        1   1     1        1   
Pharmacy                            1        1   1     1        1   
Pizza Place                         1        1   1     1        1   
Plaza                               2        2   2     2        2   
Salad Place                         1        1   1     1        1   
Salon / Barbershop                  3        3   3     3        3   
Sandwich Place                      6        6   6     6        6   
Seafood Restaurant                  3        3   3     3        3   
Smoke Shop                          1        1   1     1        1   
Snack Place                         1        0   1     1        1   
Southern / Soul Food Restaurant     1        1   1     1        1   
Spa                                 3        3   3     3        3   
Speakeasy                           1        1   1     1        1   
Steakhouse                          3        3   3     3        3   
Sushi Restaurant                    1        1   1     1        1   
Taco Place                          1        1   1     1        1   
Theater                             2        2   2     2        2   
Vegetarian / Vegan Restaurant       1        1   1     1        1   
Whisky Bar                     

### Only one asian restaurant! Below I will pull up specific information about the chinese restaurant

In [44]:
dataframe_filtered.loc[dataframe_filtered['categories'] == 'Asian Restaurant']

name        categories       address  cc        city  \
61  Momofuku CCDC  Asian Restaurant  1090 I St NW  US  Washington   

          country crossStreet  distance  \
61  United States     11th St       292   

                                     formattedAddress  \
61  [1090 I St NW (11th St), Washington, D.C. 2000...   

                                       labeledLatLngs        lat        lng  \
61  [{'label': 'display', 'lat': 38.90058120718301...  38.900581 -77.026708   

   neighborhood postalCode state                        id  
61          NaN      20001  D.C.  562c0479498e2c64fb092ae9

### Looks like Momofuku CCDC is the only asian restaurant in this cluster. Below I will visualize all businesses with Momofuku as the red marker.

In [45]:
cluster_map = folium.Map(location=[lat_7, long_7], zoom_start=15) # generate map centred around Ecco

# add popular spots to the map as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    if label == 'Asian Restaurant':
        folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        fill=True,
        color='red',
        fill_color='red',
        fill_opacity=0.6
        ).add_to(cluster_map)
    else:
        folium.features.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            fill=True,
            color='blue',
            fill_color='blue',
            fill_opacity=0.6
            ).add_to(cluster_map)

# display map
cluster_map

### Finally, let's take a closer look at Momofuku and see if we can compete with them!

In [46]:
venue_id = '562c0479498e2c64fb092ae9' # ID of Harry's Italian Pizza Bar
url_fuku = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)
url_fuku

'https://api.foursquare.com/v2/venues/562c0479498e2c64fb092ae9?client_id=1YZGINGMDDORH40PP2QN0WWPUDY5JXBOT5TL3MNKCU4NG0SN&client_secret=KMSKN0NBS15INTGFPDQC4QMYE3NVJED0XT0C5FAB0KPGJHBM&v=20180604'

### Send GET request for result and get the overall rating

In [47]:
result_fuku = requests.get(url_fuku).json()

#returns overall rating
try:
    print(result_fuku['response']['venue']['rating'])
except:
    print('This venue has not been rated yet.')

7.5


### 7.5 is a pretty high rating! We should not start the business too close to it, and put it closer to Mcphearson square. Since we only have only Momofuku as our sole competitor, we should have a good chance of succeeding putting our restaurant there. Thanks for tuning in!